# Percentiles

Assessment of model percentiles 99th, 99.5th, and 99.9th (1st, 0.5th and 0.1st for Tasmin)

In [1]:
import warnings
warnings.filterwarnings('ignore')

import sys
import numpy as np
import matplotlib.pyplot as plt
import cmocean
import cartopy.crs as ccrs

sys.path.append('/g/data/xv83/users/at2708/bias_adjustment/evaluation/npcp/results')
import utils

In [2]:
def calc_perc(da, var):
    """Calculate the averaged 5-year maximum (minimum for Tasmin)"""
    
    if var == 'pr' or var == 'tasmax':
        mode = 'upper percentiles'
        percentiles_99 = da.chunk({'time': -1}).quantile(0.99, dim='time')
        percentiles_995 = da.chunk({'time': -1}).quantile(0.995, dim='time')
        percentiles_999 = da.chunk({'time': -1}).quantile(0.999, dim='time')
        return percentiles_99, percentiles_995, percentiles_999, mode
    else:
        mode = 'lower percentiles'
        percentiles_01 = da.chunk({'time': -1}).quantile(0.01, dim='time')
        percentiles_005 = da.chunk({'time': -1}).quantile(0.005, dim='time')
        percentiles_001 = da.chunk({'time': -1}).quantile(0.001, dim='time')       
        return percentiles_01, percentiles_005, percentiles_001, mode
     

In [3]:
def get_data(var, gcm, rcm, task):
    """Get data needed for the evaluation"""

    assert gcm in ['ECMWF-ERA5', 'CSIRO-ACCESS-ESM1-5']
    assert rcm in ['BOM-BARPA-R', 'CSIRO-CCAM-2203', 'UQ-DES-CCAM-2105']
    assert task in ['historical', 'xvalidation']
    
    if gcm == 'ECMWF-ERA5':
        start_date = '2000-01-01' if task == 'xvalidation' else '1980-01-01'
    else:
        start_date = '1990-01-01' if task == 'xvalidation' else '1980-01-01' 
    end_date = '2019-12-31'
    
    da_dict = {}
    
    da_dict['obs'] = utils.get_npcp_data(
        var,
        'observations',
        'AGCD',
        'raw',
        'task-reference',
        start_date,
        end_date,
        'AU'
    )
   
    da_dict['gcm'] = utils.get_npcp_data(
        var,
        gcm,
        'GCM',
        'raw',
        'task-reference',
        start_date,
        end_date,
        'AU'
    )
    da_dict['rcm_raw'] = utils.get_npcp_data(
        var,
        gcm,
        rcm,
        'raw',
        'task-reference',
        start_date,
        end_date,
        'AU'
    )
    da_dict['rcm_ecdfm'] = utils.get_npcp_data(
        var,
        gcm,
        rcm,
        'ecdfm',
        f'task-{task}',
        start_date,
        end_date,
        'AU'
    )
    da_dict['rcm_qme'] = utils.get_npcp_data(
        var,
        gcm,
        rcm,
        'qme',
        f'task-{task}',
        start_date,
        end_date,
        'AU'
    )
    if task == 'xvalidation':
        da_dict['rcm_qdc'] = utils.get_npcp_data(
            var,
            gcm,
            rcm,
            'qdc',
            f'task-{task}',
            start_date,
            end_date,
            'AU'
        )
        
    # TODO: Add additional bias correction methods as data becomes available 

    return da_dict

In [4]:
def plot_mean_bias(ax, da_obs, da_model, var, cmap, levels, model_name, mode, percentile, ob_fractions=None):
    """Plot the mean bias for a particular model"""
    
    perc1_obs, perc2_obs, perc3_obs, _ = calc_perc(da_obs, var)  
    perc1_model, perc2_model, perc3_model, _ = calc_perc(da_model, var) 

    if (var == 'pr' or var == 'tasmax') and percentile == '99th':
        bias = perc1_model - perc1_obs #99th p.
    elif (var == 'pr' or var == 'tasmax') and percentile  == '99.5th':
        bias = perc2_model - perc2_obs #99.5th p.
    elif (var == 'pr' or var == 'tasmax') and percentile  == '99.9th':
        bias = perc3_model - perc3_obs #99.9th p.
    elif var == 'tasmin' and percentile == '1st':
        bias = perc1_model - perc1_obs #1st p.
    elif var == 'tasmin' and percentile == '0.5th':
        bias = perc2_model - perc2_obs #0.5th p.
    elif var == 'tasmin' and percentile == '0.1st':
        bias = perc3_model - perc3_obs #0.1st p.
    else:
        print('Invalid percentile value or invalid variable')
        return
    bias = utils.clip_data(bias, utils.get_aus_shape())
    if ob_fractions is not None:
        bias = utils.mask_by_pr_ob_fraction(bias, ob_fractions, threshold=0.9) 
    mae = np.nanmean(np.abs(bias))    
    units = 'mm/day' if var == 'pr' else da_model.attrs['units']
    
    im = bias.plot(
        ax=ax,
        transform=ccrs.PlateCarree(),
        cmap=cmap,
        levels=levels,
        extend='both', 
        add_colorbar=False
    ) #cbar_kwargs={'label': units},
    ax.set_title(model_name)
    ax.coastlines()
    cbar = plt.colorbar(im, ax=ax, orientation='vertical', pad=0.04)
    cbar.ax.tick_params(labelsize=14)  
    cbar.set_label(units, fontsize=14) 
    ax.text(0.02, 0.02, f'MAE: {mae:.2f} {units}', transform=ax.transAxes, fontsize=10)

In [5]:
def plot_comparison(var, gcm, rcm, task, cmap, levels):
    """Plot the complete comparison"""

    da_dict = get_data(var, gcm, rcm, task)

    if var == 'pr' or var == 'tasmax':
        percentiles = ['99th', '99.5th', '99.9th']  
        ob_fractions = utils.get_pr_weights(gcm, task) if var == 'pr' else None
    elif var == 'tasmin':
        percentiles = ['1st', '0.5th', '0.1st']
        ob_fractions = None
    else:
        print('Invalid variable')

    ncols = 5 if task == 'xvalidation' else 4
    rows, cols = len(percentiles), ncols 
    
    fig, axs = plt.subplots(rows, cols, figsize=[7*cols, 5*rows], subplot_kw={'projection': ccrs.PlateCarree()})
    
    for row, percentile in enumerate(percentiles):
        _, _, _, mode = calc_perc(da_dict['obs'], var)  # get mode "upper percentiles" or "lower percentiles"

        ax1 = axs[row, 0]
        ax2 = axs[row, 1]
        ax3 = axs[row, 2]
        ax4 = axs[row, 3]
        if task == 'xvalidation':
            ax5 = axs[row, 4]

        # Plot GCM bias
        plot_mean_bias(ax1, da_dict['obs'], da_dict['gcm'], var, cmap, levels, gcm, mode, percentile, ob_fractions=ob_fractions)
        ax1.set_title(f'{gcm} ({percentile})', fontsize=16)

        # Plot RCM raw bias
        plot_mean_bias(ax2, da_dict['obs'], da_dict['rcm_raw'], var, cmap, levels, f'{rcm} (raw)', mode, percentile, ob_fractions=ob_fractions)
        ax2.set_title(f'{rcm} (raw) ({percentile})', fontsize=16)

        # Plot RCM bias corrected bias
        plot_mean_bias(ax3, da_dict['obs'], da_dict['rcm_ecdfm'], var, cmap, levels, f'{rcm} (ecdfm)', mode, percentile, ob_fractions=ob_fractions)
        ax3.set_title(f'{rcm} (ecdfm) ({percentile})', fontsize=16)

        # Plot RCM bias corrected bias
        plot_mean_bias(ax4, da_dict['obs'], da_dict['rcm_qme'], var, cmap, levels, f'{rcm} (qme)', mode, percentile, ob_fractions=ob_fractions)
        ax4.set_title(f'{rcm} (qme) ({percentile})', fontsize=16)

        if task == 'xvalidation':
            plot_mean_bias(ax5, da_dict['obs'], da_dict['rcm_qdc'], var, cmap, levels, f'{rcm} (qdc)', mode, percentile, ob_fractions=ob_fractions)
            ax5.set_title(f'{rcm} (qdc) ({percentile})', fontsize=16)


    long_name = da_dict['rcm_raw'].attrs['long_name']
    if gcm == 'ECMWF-ERA5':
        start_year = '2000' if task == 'xvalidation' else '1980'
    else:
        start_year = '1990' if task == 'xvalidation' else '1980'
        
    plt.suptitle(mode.capitalize() + f' bias (model minus obs) for different percentiles in the {start_year}-2019 {long_name}', fontsize=18)
    plt.show()


# task-historical
Bias corrected data for the 1980-2019 period, using 1980-2019 as a training period.

In [6]:
variable = 'pr'
levels = np.arange(-27, 27.1, 5)
cmap = 'BrBG'

### ERA5

In [7]:
plot_comparison(variable, 'ECMWF-ERA5', 'BOM-BARPA-R', 'historical', cmap, levels)

In [8]:
plot_comparison(variable, 'ECMWF-ERA5', 'CSIRO-CCAM-2203', 'historical', cmap, levels)

In [9]:
plot_comparison(variable, 'ECMWF-ERA5', 'UQ-DES-CCAM-2105', 'historical', cmap, levels)

### ACCESS-ESM1-5

In [10]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'BOM-BARPA-R', 'historical', cmap, levels)

In [11]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'CSIRO-CCAM-2203', 'historical', cmap, levels)

In [12]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'UQ-DES-CCAM-2105', 'historical', cmap, levels)

# task-xvalidation

### ERA5
Bias corrected data for the 2000-2019 period, using 1980-1999 as a training period.

In [13]:
plot_comparison(variable, 'ECMWF-ERA5', 'BOM-BARPA-R', 'xvalidation', cmap, levels)

In [7]:
plot_comparison(variable, 'ECMWF-ERA5', 'CSIRO-CCAM-2203', 'xvalidation', cmap, levels)

In [8]:
plot_comparison(variable, 'ECMWF-ERA5', 'UQ-DES-CCAM-2105', 'xvalidation', cmap, levels)

### ACCESS-ESM1-5
Bias corrected data for the 1990-2019 period, using 1960-1989 as a training period.

In [9]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'BOM-BARPA-R', 'xvalidation', cmap, levels)

In [10]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'CSIRO-CCAM-2203', 'xvalidation', cmap, levels)

In [11]:
plot_comparison(variable, 'CSIRO-ACCESS-ESM1-5', 'UQ-DES-CCAM-2105', 'xvalidation', cmap, levels)